In [1]:
import json
import numpy as np
import re
from grl.p2sro.payoff_table import PayoffTable

# psro_payoff_table_checkpoint_path = "/home/jb/git/grl/grl/data/simple_push_psro/manager_08.41.48PM_Dec-28-2020/payoff_table_checkpoints/payoff_table_checkpoint_25.json"
# psro_policy_nums_path = "/home/jb/git/grl/grl/data/simple_push_psro/manager_08.41.48PM_Dec-28-2020/payoff_table_checkpoints/policy_nums_checkpoint_25.json"

# psro_payoff_table_checkpoint_path = "/home/jb/git/grl/grl/data/simple_push_psro/manager_10.59.03PM_Dec-28-2020/payoff_table_checkpoints/payoff_table_checkpoint_30.json"
# psro_policy_nums_path = "/home/jb/git/grl/grl/data/simple_push_psro/manager_10.59.03PM_Dec-28-2020/payoff_table_checkpoints/policy_nums_checkpoint_30.json"

psro_payoff_table_checkpoint_path = "/home/jb/git/grl/grl/data/kuhn_psro/manager_11.25.08PM_Jan-11-2021/payoff_table_checkpoints/payoff_table_checkpoint_99.json"
psro_policy_nums_path = "/home/jb/git/grl/grl/data/kuhn_psro/manager_11.25.08PM_Jan-11-2021/payoff_table_checkpoints/policy_nums_checkpoint_99.json"

original_date = re.search("\d\d\.\d\d.\d\d.\w\w\w\w\w\W\d\d\W\d\d\d\d", psro_payoff_table_checkpoint_path)[0]
poker_version = "kuhn_poker"

with open(psro_policy_nums_path, "r") as policy_nums_file:
    policy_nums = json.load(policy_nums_file)
largest_fixed_policy_nums = (max(policy_nums['0']['fixed_policies']), max(policy_nums['1']['fixed_policies']))

payoff_table = PayoffTable.from_json_file(json_file_path=psro_payoff_table_checkpoint_path)

In [2]:
from grl.rl_apps.kuhn_poker_p2sro.poker_utils import get_stats_for_single_payoff_table
from grl.rl_apps.kuhn_poker_p2sro.poker_multi_agent_env import PokerMultiAgentEnv
from grl.rl_apps.kuhn_poker_p2sro.config import kuhn_sac_params, kuhn_dqn_params
from ray.rllib.agents.dqn import SimpleQTorchPolicy, SIMPLE_Q_DEFAULT_CONFIG
from ray.rllib.utils import merge_dicts

env_config = {'version': poker_version, "fixed_players": True, "dummy_action_multiplier": 20}
env = PokerMultiAgentEnv(env_config=env_config)
num_players = 2

stats = get_stats_for_single_payoff_table(
    payoff_table=payoff_table,
    highest_policy_num=min(largest_fixed_policy_nums),
    # highest_policy_num=4,
    poker_env_config=env_config,
    policy_class=SimpleQTorchPolicy,
    policy_config=merge_dicts(SIMPLE_Q_DEFAULT_CONFIG, kuhn_dqn_params(action_space=env.action_space))
)




Failed to import TensorFlow. Please note that TensorFlow is not installed by default when you install TensorFlow Probability. This is so that users can decide whether to install the GPU-enabled TensorFlow package. To use TensorFlow Probability, please install the most recent version of TensorFlow, by following instructions at https://tensorflow.org/install.




Failed to import TensorFlow. Please note that TensorFlow is not installed by default when you install TensorFlow Probability. This is so that users can decide whether to install the GPU-enabled TensorFlow package. To use TensorFlow Probability, please install the most recent version of TensorFlow, by following instructions at https://tensorflow.org/install.




Failed to import TensorFlow. Please note that TensorFlow is not installed by default when you install TensorFlow Probability. This is so that users can decide whether to install the GPU-enabled TensorFlow package. To use TensorFlow Probability, please install the most r

2021-01-12 11:41:28,778	INFO services.py:1092 -- View the Ray dashboard at http://127.0.0.1:8266
2021-01-12 11:41:30,950	INFO torch_policy.py:107 -- TorchPolicy running on GPU.
2021-01-12 11:41:31,880	INFO torch_policy.py:107 -- TorchPolicy running on GPU.


In [3]:
stats

{'num_policies': [1,
  2,
  3,
  4,
  5,
  6,
  7,
  8,
  9,
  10,
  11,
  12,
  13,
  14,
  15,
  16,
  17,
  18,
  19,
  20,
  21,
  22,
  23,
  24,
  25,
  26,
  27,
  28,
  29,
  30,
  31,
  32,
  33,
  34,
  35,
  36,
  37,
  38,
  39,
  40,
  41,
  42,
  43,
  44,
  45,
  46,
  47,
  48,
  49],
 'exploitability': [0.25,
  0.41657499582630253,
  0.12678235550189168,
  0.33225052913666986,
  0.0968541971478808,
  0.04976345711861763,
  0.04284141995594892,
  0.048693167649419083,
  0.04958676067927345,
  0.0054771868783835,
  0.010422476299891792,
  0.010987935378938912,
  0.015974858327121227,
  0.013310464804816236,
  0.01083045604136798,
  0.011952249648335661,
  0.013145531306709896,
  0.013210079825861448,
  0.009863615894742772,
  0.013812050940164716,
  0.017123007148329733,
  0.012363493026060629,
  0.014369865688731581,
  0.015772008776558655,
  0.01140984743751694,
  0.01628238454632211,
  0.013768016998534749,
  0.01602310654014763,
  0.017073079868015706,
  0.0152367543

In [4]:

import itertools
import pandas as pd
import plotly.express as px
import plotly.io as pio
# pio.renderers.default = 'png'
pio.renderers.default = "browser"

df = pd.DataFrame.from_dict(data=stats)
fig = px.line(df, x="episodes", y="exploitability",
              title='Kuhn Poker PSRO Exploitability',
              # range_x=[0, int(3e6)],
              )
fig.show()

In [5]:
save_path = f"/home/jb/git/grl/grl/data/psro_stats_{poker_version}_{original_date}.json"
with open(save_path, "+w") as json_file:
    json.dump(stats, json_file)
print(f"saved to {save_path}")

saved to /home/jb/git/grl/grl/data/psro_stats_kuhn_poker_11.25.08PM_Jan-11-2021.json
